<a href="https://colab.research.google.com/github/nayanesh-reddy/MAC-unit/blob/main/openlane_RTL_to_GDS.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# RTL to GDSII with OpenLane

Run a logic design through the [OpenLane](https://github.com/The-OpenROAD-Project/OpenLane/) GDS to RTL flow targeting the [open source SKY130 PDK](https://github.com/google/skywater-pdk/).


## Install dependencies

In [ ]:
import os
import pathlib
import sys

!curl -Ls https://micro.mamba.pm/api/micromamba/linux-64/latest | tar -xvj bin/micromamba
conda_prefix_path = pathlib.Path('conda-env')
site_package_path = conda_prefix_path / 'lib/python3.7/site-packages'
sys.path.append(str(site_package_path.resolve()))
CONDA_PREFIX = str(conda_prefix_path.resolve())
PATH = os.environ['PATH']
LD_LIBRARY_PATH = os.environ.get('LD_LIBRARY_PATH', '')
%env CONDA_PREFIX={CONDA_PREFIX}
%env PATH={CONDA_PREFIX}/bin:{PATH}
%env LD_LIBRARY_PATH={CONDA_PREFIX}/lib:{LD_LIBRARY_PATH}
!bin/micromamba create --yes --prefix $CONDA_PREFIX
!echo 'python ==3.7*' >> {CONDA_PREFIX}/conda-meta/pinned
!bin/micromamba install --yes --prefix $CONDA_PREFIX \
                        --channel litex-hub \
                        --channel main \
                        open_pdks.sky130a \
                        magic \
                        openroad \
                        netgen \
                        yosys 
!bin/micromamba install --yes --prefix $CONDA_PREFIX \
                        --channel conda-forge \
                        tcllib gdstk pyyaml click

bin/micromamba
env: CONDA_PREFIX=/content/conda-env
env: PATH=/content/conda-env/bin:/opt/bin:/usr/local/nvidia/bin:/usr/local/cuda/bin:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/tools/node/bin:/tools/google-cloud-sdk/bin
env: LD_LIBRARY_PATH=/content/conda-env/lib:/usr/local/nvidia/lib:/usr/local/nvidia/lib64

                                           __
          __  ______ ___  ____ _____ ___  / /_  ____ _
         / / / / __ `__ \/ __ `/ __ `__ \/ __ \/ __ `/
        / /_/ / / / / / / /_/ / / / / / / /_/ / /_/ /
       / .___/_/ /_/ /_/\__,_/_/ /_/ /_/_.___/\__,_/
      /_/

Empty environment created at prefix: /content/conda-env

                                           __
          __  ______ ___  ____ _____ ___  / /_  ____ _
         / / / / __ `__ \/ __ `/ __ `__ \/ __ \/ __ `/
        / /_/ / / / / / / /_/ / / / / / / /_/ / /_/ /
       / .___/_/ /_/ /_/\__,_/_/ /_/ /_/_.___/\__,_/
      /_/

[+] 0.0s
[+] 0.1s
litex-hub/linux-64  ⣾  
litex-hub/noarch    ⣾

## Get OpenLane

In [ ]:
!git clone --depth=1 https://github.com/The-OpenROAD-Project/OpenLane

Cloning into 'OpenLane'...
remote: Enumerating objects: 503, done.
remote: Counting objects: 100% (503/503), done.
remote: Compressing objects: 100% (429/429), done.
remote: Total 503 (delta 77), reused 291 (delta 26), pack-reused 0
Receiving objects: 100% (503/503), 3.03 MiB | 15.89 MiB/s, done.
Resolving deltas: 100% (77/77), done.


## Write verilog

In [ ]:
%%writefile MAC.v
module MAC(a, b, out, rst, clk);
  
  input [7:0] a, b;
  input clk, rst;
  
  output reg [15:0] out;
  
  always @(posedge clk)
    begin
      if(rst)
        out <= 0;
      else
        out <= out + (a*b);
    end

endmodule

Writing MAC.v


## Write configuration

In [ ]:
%%writefile config.tcl
set ::env(DESIGN_NAME) MAC

set ::env(VERILOG_FILES) "MAC.v"

set ::env(CLOCK_TREE_SYNTH) 1
set ::env(CLOCK_PORT) "clk"

set ::env(PL_RANDOM_GLB_PLACEMENT) 1

set ::env(FP_SIZING) absolute
set ::env(DIE_AREA) "0 0 200 200"
set ::env(PL_TARGET_DENSITY) 0.90


set ::env(FP_PDN_HORIZONTAL_HALO) 6
set ::env(FP_PDN_VERTICAL_HALO) 6

set ::env(DIODE_INSERTION_STRATEGY) 3

# disable klayout because of https://github.com/hdl/conda-eda/issues/175
set ::env(RUN_KLAYOUT) 0
# disable CVC because of https://github.com/hdl/conda-eda/issues/174
set ::env(RUN_CVC) 0

Overwriting config.tcl


## Run OpenLane Flow

In [ ]:
import os
import pathlib
OPENLANE_ROOT=str(pathlib.Path('OpenLane').resolve())
PATH=os.environ['PATH']
%env PDK_ROOT={CONDA_PREFIX}/share/pdk
%env PDK=sky130A
%env STD_CELL_LIBRARY=sky130_fd_sc_hd
%env STD_CELL_LIBRARY_OPT=sky130_fd_sc_hd
%env TCLLIBPATH={CONDA_PREFIX}/lib/tcllib1.20
%env OPENLANE_ROOT={OPENLANE_ROOT}
%env PATH={PATH}:{OPENLANE_ROOT}:{OPENLANE_ROOT}/scripts
%env OPENLANE_LOCAL_INSTALL=1
!flow.tcl -design . -ignore_mismatches

env: PDK_ROOT=/content/conda-env/share/pdk
env: PDK=sky130A
env: STD_CELL_LIBRARY=sky130_fd_sc_hd
env: STD_CELL_LIBRARY_OPT=sky130_fd_sc_hd
env: TCLLIBPATH=/content/conda-env/lib/tcllib1.20
env: OPENLANE_ROOT=/content/OpenLane
env: PATH=/content/conda-env/bin:/opt/bin:/usr/local/nvidia/bin:/usr/local/cuda/bin:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/tools/node/bin:/tools/google-cloud-sdk/bin:/content/OpenLane:/content/OpenLane/scripts
env: OPENLANE_LOCAL_INSTALL=1
OpenLane 41ed0036c3dc77961a34005fc7e4494881f0a07f
All rights reserved. (c) 2020-2022 Efabless Corporation and contributors.
Available under the Apache License, version 2.0. See the LICENSE file for more details.

[WARNING]: OpenLane may not function properly: 'OL_INSTALL_DIR'
The version of open_pdks used in building the PDK does not match the version OpenLane was tested on (installed: 002b5dd29d81e9affec60cb6d57ed867c888e23c, tested: 0059588eebfc704681dc2368bd1d33d96281d10f)
This may introduce some issue

## Dump flow report

In [ ]:
import pandas as pd
import pathlib

pd.options.display.max_rows = None
final_summary_reports = sorted(pathlib.Path('runs').glob('*/reports/metrics.csv'))
df = pd.read_csv(final_summary_reports[-1])
df.transpose()

0
design                                     /content
design_name                                     MAC
config                      RUN_2022.10.31_17.13.55
flow_status                          flow completed
total_runtime                            0h3m45s0ms
routed_runtime                           0h2m58s0ms
(Cell/mm^2)/Core_Util                          -2.0
DIEAREA_mm^2                                   0.04
CellPer_mm^2                                     -1
OpenDP_Util                                      -1
Peak_Memory_Usage_MB                         536.05
cell_count                                       -1
tritonRoute_violations                            0
Short_violations                                  0
MetSpc_violations                                 0
OffGrid_violations                                0
MinHole_violations                                0
Other_violations                                  0
Magic_violations                                  0
antenna_violations                               -1
lvs_total_errors                                  0
cvc_total_errors                                 -1
klayout_violations                               -1
wire_length                                   96125
vias                                           5922
wns                                             0.0
pl_wns                                           -1
optimized_wns                                   0.0
fastroute_wns                                   0.0
spef_wns                                        0.0
tns                                             0.0
pl_tns                                           -1
optimized_tns                                   0.0
fastroute_tns                                   0.0
spef_tns                                        0.0
HPWL                                             -1
routing_layer1_pct                              0.0
routing_layer2_pct                            54.11
routing_layer3_pct                            62.93
routing_layer4_pct                             37.9
routing_layer5_pct                            42.19
routing_layer6_pct                             5.43
wires_count                                     434
wire_bits                                       553
public_wires_count                                5
public_wire_bits                                 34
memories_count                                    0
memory_bits                                       0
processes_count                                   0
cells_pre_abc                                   455
AND                                              50
DFF                                               0
NAND                                             35
NOR                                              10
OR                                               48
XOR                                             114
XNOR                                             32
MUX                                              16
inputs                                           33
outputs                                          16
level                                            17
EndCaps                                         130
TapCells                                        469
Diodes                                            0
Total_Physical_Cells                            599
CoreArea_um^2                              33344.48
power_slowest_internal_uW                        -1
power_slowest_switching_uW                       -1
power_slowest_leakage_uW                         -1
power_typical_internal_uW                        -1
power_typical_switching_uW                       -1
power_typical_leakage_uW                         -1
power_fastest_internal_uW                        -1
power_fastest_switching_uW                       -1
power_fastest_leakage_uW                         -1
critical_path_ns                                 -1
suggested_clock_period                        

## Display layout

In [ ]:
import pathlib
import gdstk
import IPython.display

gdss = sorted(pathlib.Path('runs').glob('*/results/final/gds/*.gds'))
library = gdstk.read_gds(gdss[-1])
top_cells = library.top_level()
top_cells[0].write_svg('MAC.svg')
IPython.display.SVG('MAC.svg')

# Generate STL files for GDSII 3D render

Video : [Zero To ASIC Course - Maximo shows how to make beautiful GDS renders with Blender](https://www.youtube.com/watch?v=gBjQI3GrBHU&t=711s&ab_channel=ZeroToASICCourse)


## Get gdsiistl

[gdsiistl](https://github.com/mbalestrini/gdsiistl) - Converts GDSII files to STL files. This version of gdsiistl is adapted to work with the GDS files generated for the SkyWater SKY130 PDK.

In [ ]:
!git clone https://github.com/mbalestrini/gdsiistl

Cloning into 'gdsiistl'...
remote: Enumerating objects: 64, done.
remote: Counting objects: 100% (64/64), done.
remote: Compressing objects: 100% (44/44), done.
remote: Total 64 (delta 29), reused 44 (delta 15), pack-reused 0
Unpacking objects: 100% (64/64), done.


In [ ]:
!pip install -r gdsiistl/requirements.txt

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.7/157.7 kB 5.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 32.9 MB/s eta 0:00:00
  Created wheel for gdspy: filename=gdspy-1.6.12-cp37-cp37m-linux_x86_64.whl size=499908 sha256=caa3eef3588e7b129af3b722035ca9ca64e52f37d51d76a1b0b82cd1e8e2c281
  Stored in directory: /root/.cache/pip/wheels/75/12/07/1bdbde024f258e40958b46e22ddb21802183e604405bb9dcb2
Successfully built gdspy


## Skywater 130nm Layers


![skywater_layers.png](https://www.zerotoasiccourse.com/stackup.png)

In [ ]:
# choose which GDSII layers to use

%%writefile layers.py
layerstack = {
    # (layernumber, datatype) : (zmin, zmax, 'layername'),
    
    (235,4): (0, 0.4, 'substrate'),

    (64,20): (0.4 - 0.2, 0.4, 'nwell'),    
    #(65,44): (0, 0.1, 'tap'),    
    (65,20): (0.4 - 0.12, 0.4, 'diff'),    
    (66,20): (0.4, 0.4 + 0.002 + 0.18, 'poly'),    
    (66,44): (0.4, 0.4 + 0.9361, 'licon'),    
    (67,20): (1.3361, 1.3361 + 0.1, 'li'),    
    (67,44): (1.4361, 1.4361 + 0.265 + 0.075, 'mcon'),    
    (68,20): (1.7761, 1.7761 + 0.36, 'met1'),    
    (68,44): (2.1361, 2.1361 + 0.27, 'via1'),    
    (69,20): (2.4061, 2.4061 + 0.36, 'met2'),    
    (69,44): (2.7661, 2.7661 + 0.42, 'via2'),    
    (70,20): (3.1861, 3.1861 + 0.845, 'met3'),    
    (70,44): (4.0311, 4.0311 + 0.39, 'via3'),    
    (71,20): (4.4211, 4.4211 + 0.845, 'met4'),    
    (71,44): (5.2661, 5.2661 + 0.505, 'via4'),    
    (72,20): (5.7711, 5.7711 + 1.26, 'met5'),
    # (83,44): (0, 0.1, 'text'),



}

Writing layers.py


In [ ]:
# Replace the above layerstack dictionary with the layerstack in gdsiistl.py file

!sed -i '/layerstack = {/,/}/d' /content/gdsiistl/gdsiistl.py 
!sed -i '/# choose which GDSII layers to use/r layers.py' /content/gdsiistl/gdsiistl.py

In [ ]:
# Create a directory for STL files of GDS

gds_path = str(gdss[-1])
!mkdir -p gds_stl_files
!cp -r $gds_path gds_stl_files/.

## Convert GDSII to STL files

In [ ]:
!python gdsiistl/gdsiistl.py /content/gds_stl_files/MAC.gds

Reading GDSII file /content/gds_stl_files/MAC.gds...
Extracting polygons...
Triangulating polygons...
Extruding polygons and writing to files...
    ((68, 20), met1) to /content/gds_stl_files/MAC.gds_met1.stl
    ((67, 20), li) to /content/gds_stl_files/MAC.gds_li.stl
    ((235, 4), substrate) to /content/gds_stl_files/MAC.gds_substrate.stl
    ((67, 44), mcon) to /content/gds_stl_files/MAC.gds_mcon.stl
    ((68, 44), via1) to /content/gds_stl_files/MAC.gds_via1.stl
    ((69, 20), met2) to /content/gds_stl_files/MAC.gds_met2.stl
    ((69, 44), via2) to /content/gds_stl_files/MAC.gds_via2.stl
    ((70, 20), met3) to /content/gds_stl_files/MAC.gds_met3.stl
    ((70, 44), via3) to /content/gds_stl_files/MAC.gds_via3.stl
    ((71, 20), met4) to /content/gds_stl_files/MAC.gds_met4.stl
    ((71, 44), via4) to /content/gds_stl_files/MAC.gds_via4.stl
    ((72, 20), met5) to /content/gds_stl_files/MAC.gds_met5.stl
    ((65, 20), diff) to /content/gds_stl_files/MAC.gds_diff.stl
    ((66, 44), li

## Download the zip file of STL

In [ ]:
# Zip the folder
!zip -r /content/MAC_gds_stl_files.zip /content/gds_stl_files

# Download the zip folder of gds stl files
from google.colab import files
files.download('/content/MAC_gds_stl_files.zip')

  adding: content/gds_stl_files/ (stored 0%)
  adding: content/gds_stl_files/MAC.gds_poly.stl (deflated 83%)
  adding: content/gds_stl_files/MAC.gds_via2.stl (deflated 86%)
  adding: content/gds_stl_files/MAC.gds_met2.stl (deflated 84%)
  adding: content/gds_stl_files/MAC.gds_licon.stl (deflated 86%)
  adding: content/gds_stl_files/MAC.gds_via3.stl (deflated 86%)
  adding: content/gds_stl_files/MAC.gds_via1.stl (deflated 86%)
  adding: content/gds_stl_files/MAC.gds_nwell.stl (deflated 85%)
  adding: content/gds_stl_files/MAC.gds_met5.stl (deflated 80%)
  adding: content/gds_stl_files/MAC.gds_via4.stl (deflated 83%)
  adding: content/gds_stl_files/MAC.gds_met3.stl (deflated 84%)
  adding: content/gds_stl_files/MAC.gds_met1.stl (deflated 85%)
  adding: content/gds_stl_files/MAC.gds_li.stl (deflated 82%)
  adding: content/gds_stl_files/MAC.gds_substrate.stl (deflated 68%)
  adding: content/gds_stl_files/MAC.gds_mcon.stl (deflated 87%)
  adding: content/gds_stl_files/MAC.gds_diff.stl (defl

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>